### Imports

In [1]:
import numpy as np
import scipy.sparse as sp
import torch
import torch.nn as nn
import pickle as pkl
import networkx as nx

from tqdm import tqdm
from DGI.models import DGI, LogReg
from DGI.utils import process
from tensorflow.keras.optimizers import Adam, Nadam

from scripts.utils import *

/Users/zohairshafi/miniforge3/lib/python3.10/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


### Class Definitions

In [2]:
class BaseEmbedder:
    def __init__(self, graph, embed_shape = (128,)):
        self.embed(graph)
        self.E = list(graph.edges())
        self.graph = graph
        self.embed_shape = embed_shape
    
    def embed(self, graph):
        raise NotImplementedError
    
    def get_embedding(self):
        raise NotImplementedError
        

In [35]:
class DGIEmbedding(BaseEmbedder):
    def __init__(self, embed_dim = 64, graph = None, feature_matrix = None, use_xm = False, debug = False, batch_size = 1, nb_epochs = 2500, patience = 20, ortho_ = 0.1, sparse_ = 0.1, lr = 1e-3, l2_coef = 0.0, drop_prob = 0.0, sparse = True, nonlinearity = 'prelu', model_name = ''):

        self.embed_dim = embed_dim
        self.debug = debug
        
        # Training Params
        self.graph = graph
        self.batch_size = batch_size
        self.nb_epochs = nb_epochs
        self.patience = patience
        self.lr = lr
        self.l2_coef = l2_coef
        self.feature_matrix = feature_matrix
        self.drop_prob = drop_prob
        self.hid_units = embed_dim
        self.sparse = sparse
        self.nonlinearity = nonlinearity
        self.use_xm = use_xm
        self.ortho_ = ortho_
        self.sparse_ = sparse_
        self.model_name = model_name

        self.time_per_epoch = None
        
        if graph is not None:
            self.embed()
        else:
            self.graph = None
    
    def embed(self):

        
        if self.feature_matrix is None:
            feature_matrix = np.identity(len(self.graph))
        else: 
            feature_matrix = self.feature_matrix

        adj = nx.to_scipy_sparse_array(self.graph)
        features = sp.lil_matrix(feature_matrix)
        features, _ = process.preprocess_features(features)

        nb_nodes = features.shape[0]
        ft_size = features.shape[1]

        adj = process.normalize_adj(adj + sp.eye(adj.shape[0]))

        if self.sparse:
            sp_adj = process.sparse_mx_to_torch_sparse_tensor(adj)
        else:
            adj = (adj + sp.eye(adj.shape[0])).todense()

        features = torch.FloatTensor(features[np.newaxis])
        if not self.sparse:
            adj = torch.FloatTensor(adj[np.newaxis])
            if torch.cuda.is_available():
                adj = adj.cuda()

        if self.feature_matrix is not None: 
            sense_features = torch.FloatTensor(self.feature_matrix)
            if torch.cuda.is_available():
                sense_features = sense_features.cuda()


        model = DGI(ft_size, self.hid_units, self.nonlinearity)
        if torch.cuda.is_available():
            model = model.cuda()
        optimiser = torch.optim.Adam(model.parameters(), lr = self.lr, weight_decay = self.l2_coef)

        b_xent = nn.BCEWithLogitsLoss()
        xent = nn.CrossEntropyLoss()
        cnt_wait = 0
        best = 1e9
        best_t = 0
        
        start_time = time.time()
        for epoch in tqdm(range(self.nb_epochs)):
            model.train()
            optimiser.zero_grad()

            idx = np.random.permutation(nb_nodes)
            shuf_fts = features[:, idx, :]

            lbl_1 = torch.ones(self.batch_size, nb_nodes)
            lbl_2 = torch.zeros(self.batch_size, nb_nodes)
            lbl = torch.cat((lbl_1, lbl_2), 1)

            if torch.cuda.is_available():
                shuf_fts = shuf_fts.cuda()
                lbl = lbl.cuda()
                sp_adj = sp_adj.cuda()
                features = features.cuda()
            
            logits = model(features, shuf_fts, sp_adj if self.sparse else adj, self.sparse, None, None, None) 
            
            if self.use_xm == True and feature_matrix is not None:
                
                start_idx = 0
                loop = True
                
                ortho_loss = 0
                sparse_loss = 0
                xm_batch_size = 1024
                
                sf = sense_features
                embeds, _ = model.embed(sf, sp_adj if self.sparse else adj, self.sparse, None)
                                
                while loop:
                    end_idx = start_idx + xm_batch_size
                    if end_idx > len(self.graph):
                        loop = False
                        end_idx = len(self.graph)
                        
                    
                    sf = sense_features[start_idx : end_idx]
                    embeds_ = torch.squeeze(embeds)[start_idx : end_idx]
                    
                    
                    sense_mat = torch.einsum('ij, ik -> ijk', embeds_, sf)
                    E = sense_mat
                    y_norm = torch.diagonal(torch.matmul(embeds_, torch.transpose(embeds_, 0, 1)))
                    sense_norm = torch.diagonal(torch.matmul(sf, torch.transpose(sf, 0, 1)))
                    norm = torch.multiply(y_norm, sense_norm)
                    E = torch.transpose(torch.transpose(E, 0, 2) / norm, 0, 2)
                    E = (E - torch.amin(E, dim = [-1, -2], keepdim = True)) / (torch.amax(E, dim = [-1, -2], keepdim = True) - torch.amin(E, dim = [-1, -2], keepdim = True))

                    E_t = torch.transpose(E, 1, 2)
                    E_o = torch.einsum('aij, ajh -> aih', E, E_t)
                    E_o = torch.sum(E_o)
                    batch_ortho_loss = (self.ortho_ * E_o) / self.batch_size

                    batch_sparse_loss = (self.sparse_ * torch.sum(torch.linalg.norm(E, ord = 1, axis = 0))) / self.batch_size
                        
                    ortho_loss += batch_ortho_loss
                    sparse_loss += batch_sparse_loss
                    
                    start_idx = end_idx
                    
                loss = b_xent(logits, lbl) + ortho_loss + sparse_loss
            else:
                loss = b_xent(logits, lbl)

            if self.debug:
                print('Loss:', loss)

            if loss < best:
                best = loss
                best_t = epoch
                cnt_wait = 0
                torch.save(model.state_dict(), self.model_name + '.pkl')
            else:
                cnt_wait += 1

            if cnt_wait == self.patience:
                if self.debug: 
                    print('Early stopping!')
                break

            loss.backward()
            optimiser.step()
            
        self.time_per_epoch = (time.time() - start_time) / epoch

        if self.debug: 
            print('Loading {}th epoch'.format(best_t))
        model.load_state_dict(torch.load(self.model_name + '.pkl'))

        self.node_model = model
        self.fitted = True

        embeds, _ = model.embed(features, sp_adj if self.sparse else adj, self.sparse, None)
        self.embeddings = embeds
    
    def get_embedding(self):
        if torch.cuda.is_available():
            return np.squeeze(self.embeddings.cpu().numpy())
        return np.squeeze(self.embeddings.numpy())
    




In [ ]:
with open('./data/squirrel.pkl', 'rb') as file: 
    graph_dict = pkl.load(file)
    
graph = nx.Graph(nx.to_numpy_array(graph_dict))    
graph = nx.Graph(nx.to_numpy_array(graph))


In [36]:
# with open('./data/squirrel.pkl', 'rb') as file: 
#     graph_dict = pkl.load(file)
    
# graph = nx.Graph(nx.to_numpy_array(graph_dict))    
# graph = nx.Graph(nx.to_numpy_array(graph))

# graph = generate_graph(graph_type = 'ba',
#                            num_nodes = 1000,
#                            param = [5, 0.02],
#                            weights = 'Equal')

graph = nx.karate_club_graph()


sense_feat_dict, sense_features = get_sense_features(graph, ppr_flag = 'std')


34it [00:00, 22596.47it/s]


/Users/zohairshafi/miniforge3/lib/python3.10/site-packages/networkx/algorithms/centrality/katz.py:325: FutureWarning:

adjacency_matrix will return a scipy.sparse array instead of a matrix in Networkx 3.0.



In [37]:
uncorrelated_feats = ['Degree',
                    'Clustering Coefficient',
                    'Personalized Page Rank - Standard Deviation',
                    'Average Neighbor Degree',
                    'Average Neighbor Clustering',
                    'Eccentricity',
                    'Katz Centrality']
sense_features = sense_features[:, [list(sense_feat_dict).index(feat) for feat in uncorrelated_feats]]
sense_feat_dict = {feat : idx for idx, feat in enumerate(uncorrelated_feats)}

In [101]:
# dgi_og = DGIEmbedding(graph = graph, 
#            embed_dim = 16, 
#            feature_matrix = np.identity(len(graph)), 
#            use_xm = False, 
#            ortho_ = 0, 
#            sparse_ = 0, 
#            batch_size = 1, 
#            model_name = '-')
# embed_og = dgi_og.get_embedding()
# embed_og = (embed_og - np.min(embed_og)) / np.ptp(embed_og)
# feature_dict_og = find_feature_membership(input_embed = embed_og,
#                                                     embed_name = 'DGI-SF',
#                                                     sense_features = sense_features,
#                                                     sense_feat_dict = sense_feat_dict,
#                                                     top_k = 8,
#                                                     solver = 'nmf')

# explain_og = feature_dict_og['explain_norm']
# error_og = sense_features * np.log((sense_features + 1e-10) / ((embed_og @ feature_dict_og['explain_norm']) + 1e-10)) - sense_features + (embed_og @ feature_dict_og['explain_norm'])
# explain_og = (explain_og - np.min(explain_og)) / np.ptp(explain_og)


dgi_plus = DGIEmbedding(graph = graph, 
           embed_dim = 16, 
           feature_matrix = sense_features, 
           use_xm = True, 
           ortho_ = 1, 
           sparse_ = 1e-3, 
           batch_size = 1, 
           model_name = '-', 
           patience = 500)
embed_plus = dgi_plus.get_embedding()
embed_plus = (embed_plus - np.min(embed_plus)) / np.ptp(embed_plus)
feature_dict_plus = find_feature_membership(input_embed = embed_plus,
                                                    embed_name = 'DGI+XM',
                                                    sense_features = sense_features,
                                                    sense_feat_dict = sense_feat_dict,
                                                    top_k = 8,
                                                    solver = 'nmf')

explain_plus = feature_dict_plus['explain_norm']
error_plus = sense_features * np.log((sense_features + 1e-10) / ((embed_plus @ feature_dict_plus['explain_norm']) + 1e-10)) - sense_features + (embed_plus @ feature_dict_plus['explain_norm'])
explain_plus = (explain_plus - np.min(explain_plus)) / np.ptp(explain_plus)

 36%|██████████████▌                          | 888/2500 [00:01<00:02, 738.08it/s]


In [102]:
Y_og = embed_og
sense_mat = tf.einsum('ij, ik -> ijk', Y_og, sense_features)
Y_og_norm = tf.linalg.diag_part(tf.matmul(Y_og, Y_og, transpose_b = True), k = 0)
sense_norm = tf.linalg.diag_part(tf.matmul(sense_features, sense_features, transpose_b = True), k = 0)
norm = Y_og_norm * tf.cast(sense_norm, tf.float32)
D_og = tf.transpose(tf.transpose(sense_mat) / norm)
D_og = (D_og - tf.reshape(tf.reduce_min(D_og, axis = [-1, -2]), (-1, 1, 1))) / tf.reshape(tf.reduce_max(D_og, axis = [-1, -2]) - tf.reduce_min(D_og, axis = [-1, -2]), (-1, 1, 1))

Y_plus = embed_plus
sense_mat = tf.einsum('ij, ik -> ijk', Y_plus, sense_features)
Y_plus_norm = tf.linalg.diag_part(tf.matmul(Y_plus, Y_plus, transpose_b = True), k = 0)
sense_norm = tf.linalg.diag_part(tf.matmul(sense_features, sense_features, transpose_b = True), k = 0)
norm = Y_plus_norm * tf.cast(sense_norm, tf.float32)
D_plus = tf.transpose(tf.transpose(sense_mat) / norm)
D_plus = (D_plus - tf.reshape(tf.reduce_min(D_plus, axis = [-1, -2]), (-1, 1, 1))) / tf.reshape(tf.reduce_max(D_plus, axis = [-1, -2]) - tf.reduce_min(D_plus, axis = [-1, -2]), (-1, 1, 1))

norm_og = [np.linalg.norm(D_og[node, :, :], ord = 'nuc') for node in tqdm(range(len(graph)))]
norm_plus = [np.linalg.norm(D_plus[node, :, :], ord = 'nuc') for node in tqdm(range(len(graph)))]

orth_og = np.squeeze(tf.reduce_sum(D_og @ tf.transpose(D_og, perm = (0, 2, 1)), axis = [1, 2]))
orth_plus = np.squeeze(tf.reduce_sum(D_plus @ tf.transpose(D_plus, perm = (0, 2, 1)), axis = [1, 2]))


100%|████████████████████████████████████████████| 34/34 [00:00<00:00, 968.47it/s]


In [103]:
np.mean(norm_plus)

2.4509974

In [12]:
deg = dict(graph.degree)

In [15]:
max(list(deg.values()))

139

In [17]:
for n, d in deg.items():
    if d == max(list(deg.values())):
        print ("max:", n)
    if d == min(list(deg.values())):
        print ("min:", n)

max: 6
min: 228
min: 255
min: 277
min: 288
min: 302
min: 306
min: 329
min: 338
min: 339
min: 346
min: 347
min: 375
min: 391
min: 411
min: 413
min: 449
min: 453
min: 458
min: 464
min: 466
min: 471
min: 478
min: 481
min: 485
min: 502
min: 504
min: 505
min: 512
min: 516
min: 525
min: 534
min: 537
min: 539
min: 541
min: 545
min: 549
min: 550
min: 561
min: 569
min: 573
min: 579
min: 580
min: 583
min: 587
min: 590
min: 597
min: 601
min: 604
min: 611
min: 612
min: 614
min: 617
min: 619
min: 620
min: 621
min: 624
min: 626
min: 627
min: 628
min: 633
min: 638
min: 640
min: 652
min: 654
min: 656
min: 659
min: 663
min: 666
min: 669
min: 670
min: 671
min: 673
min: 677
min: 678
min: 679
min: 682
min: 683
min: 684
min: 685
min: 687
min: 689
min: 691
min: 694
min: 696
min: 697
min: 700
min: 707
min: 708
min: 711
min: 715
min: 716
min: 718
min: 720
min: 724
min: 727
min: 729
min: 731
min: 732
min: 734
min: 739
min: 741
min: 744
min: 745
min: 746
min: 747
min: 748
min: 750
min: 755
min: 758
min: 759
min

In [107]:
node = 11
fig = go.Figure()
fig.add_trace(go.Heatmap(z = D_og[node, :, :],
                         x = list(sense_feat_dict), 
                         ))
fig.update_layout(title_text = '', 
                  xaxis_title_text = 'Sense Features', 
                  yaxis_title_text = 'Dimensions', 
                  font = dict(size =  25), 
                  width = 1000, 
                  height = 1000)

fig.show()

fig = go.Figure()
fig.add_trace(go.Heatmap(z = D_plus[node, :, :],
                         x = list(sense_feat_dict), 
                         ))
fig.update_layout(title_text = '', 
                  xaxis_title_text = 'Sense Features', 
                  yaxis_title_text = 'Dimensions', 
                  font = dict(size =  25), 
                  width = 1000, 
                  height = 1000)

fig.show()


In [20]:
a = [20, 14, 3, 13, 4, 2, 8, 1, 18, 12, 22, 5, 6, 7, 11, 17]
group_a = [x - 1 for x in a]
b = list(range(34))
group_b = [x for x in b if x not in group_a]

In [36]:
colors = ['grey' if n in group_b else 'darkgrey' for n in range(34)]
shapes = ['circle-open' if n in group_b else 'square' for n in range(34)]

In [43]:
fig = go.Figure()
fig.add_trace(go.Scatter(x = edge_viz[:, 0],
                         y = edge_viz[:, 1],
                         mode = 'markers+text',
                         marker = dict(size = 40,
                                       color = colors, 
                                       symbol = shapes, 
                                      ), 
                         text = [str(x+1) for x in range(34)]))

fig.update_layout(title_text = '',
                  paper_bgcolor = 'rgba(0,0,0,0)',
                  plot_bgcolor = 'rgba(0,0,0,0)'),
fig.show()

### Large Tests - Remove

In [6]:
results = {}

for run in tqdm(range(2)):
    for d in [16, 32, 64, 128, 256]:

        results[d] = {}

        dgi_og = DGIEmbedding(graph = graph, 
                   embed_dim = d, 
                   feature_matrix = sense_features, 
                   use_xm = False, 
                   ortho_ = 0, 
                   sparse_ = 0, 
                   batch_size = 1, 
                   model_name = '-')
        embed_og = dgi_og.get_embedding()
        embed_og = (embed_og - np.min(embed_og)) / np.ptp(embed_og)
        feature_dict_og = find_feature_membership(input_embed = embed_og,
                                                            embed_name = 'DGI-SF',
                                                            sense_features = sense_features,
                                                            sense_feat_dict = sense_feat_dict,
                                                            top_k = 8,
                                                            solver = 'nmf')

        explain_og = feature_dict_og['explain_norm']
        error_og = sense_features * np.log((sense_features + 1e-10) / ((embed_og @ feature_dict_og['explain_norm']) + 1e-10)) - sense_features + (embed_og @ feature_dict_og['explain_norm'])
        explain_og = (explain_og - np.min(explain_og)) / np.ptp(explain_og)


        dgi_plus = DGIEmbedding(graph = graph, 
                   embed_dim = d, 
                   feature_matrix = sense_features, 
                   use_xm = True, 
                   ortho_ = 100, 
                   sparse_ = 1e-2, 
                   batch_size = 1, 
                   model_name = '-', 
                   patience = 500)
        embed_plus = dgi_plus.get_embedding()
        embed_plus = (embed_plus - np.min(embed_plus)) / np.ptp(embed_plus)
        feature_dict_plus = find_feature_membership(input_embed = embed_plus,
                                                            embed_name = 'DGI+XM',
                                                            sense_features = sense_features,
                                                            sense_feat_dict = sense_feat_dict,
                                                            top_k = 8,
                                                            solver = 'nmf')

        explain_plus = feature_dict_plus['explain_norm']
        error_plus = sense_features * np.log((sense_features + 1e-10) / ((embed_plus @ feature_dict_plus['explain_norm']) + 1e-10)) - sense_features + (embed_plus @ feature_dict_plus['explain_norm'])
        explain_plus = (explain_plus - np.min(explain_plus)) / np.ptp(explain_plus)


        Y_plus = embed_plus
        sense_mat = tf.einsum('ij, ik -> ijk', Y_plus, sense_features)
        Y_plus_norm = tf.linalg.diag_part(tf.matmul(Y_plus, Y_plus, transpose_b = True), k = 0)
        sense_norm = tf.linalg.diag_part(tf.matmul(sense_features, sense_features, transpose_b = True), k = 0)
        norm = Y_plus_norm * tf.cast(sense_norm, tf.float32)
        D_plus = tf.transpose(tf.transpose(sense_mat) / norm)
        D_plus = (D_plus - tf.reshape(tf.reduce_min(D_plus, axis = [-1, -2]), (-1, 1, 1))) / tf.reshape(tf.reduce_max(D_plus, axis = [-1, -2]) - tf.reduce_min(D_plus, axis = [-1, -2]), (-1, 1, 1))


        Y_og = embed_og
        sense_mat = tf.einsum('ij, ik -> ijk', Y_og, sense_features)
        Y_og_norm = tf.linalg.diag_part(tf.matmul(Y_og, Y_og, transpose_b = True), k = 0)
        sense_norm = tf.linalg.diag_part(tf.matmul(sense_features, sense_features, transpose_b = True), k = 0)
        norm = Y_og_norm * tf.cast(sense_norm, tf.float32)
        D_og = tf.transpose(tf.transpose(sense_mat) / norm)
        D_og = (D_og - tf.reshape(tf.reduce_min(D_og, axis = [-1, -2]), (-1, 1, 1))) / tf.reshape(tf.reduce_max(D_og, axis = [-1, -2]) - tf.reduce_min(D_og, axis = [-1, -2]), (-1, 1, 1))

        norm_og = [np.linalg.norm(D_og[node, :, :], ord = 'nuc') for node in tqdm(range(len(graph)))]
        norm_plus = [np.linalg.norm(D_plus[node, :, :], ord = 'nuc') for node in tqdm(range(len(graph)))]
        
        orth_og = np.squeeze(tf.reduce_sum(D_og @ tf.transpose(D_og, perm = (0, 2, 1)), axis = [1, 2]))
        orth_plus = np.squeeze(tf.reduce_sum(D_plus @ tf.transpose(D_plus, perm = (0, 2, 1)), axis = [1, 2]))

        explain_og_norm = np.linalg.norm(explain_og, ord = 'nuc')
        explain_plus_norm = np.linalg.norm(explain_plus, ord = 'nuc')

        try:
            results[d]['norm_og'].append(norm_og)
            results[d]['norm_plus'].append(norm_plus)
            results[d]['orth_og'].append(orth_og)
            results[d]['orth_plus'].append(orth_plus)
            results[d]['explain_og_norm'].append(explain_og_norm)
            results[d]['explain_plus_norm'].append(explain_plus_norm)
            results[d]['dgi_og_time'].append(dgi_og.time_per_epoch)
            results[d]['dgi+xm_time'].append(dgi_plus.time_per_epoch)
            results[d]['error_og'].append(error_og)
            results[d]['error_plus'].append(error_plus)

            results[d]['embed_og'].append(embed_og)
            results[d]['embed_plus'].append(embed_plus)


        except: 
            results[d]['norm_og'] = [norm_og]
            results[d]['norm_plus'] = [norm_plus]
            results[d]['orth_og'] = [orth_og]
            results[d]['orth_plus'] = [orth_plus]
            results[d]['explain_og_norm'] = [explain_og_norm]
            results[d]['explain_plus_norm'] = [explain_plus_norm]
            results[d]['dgi_og_time'] = [dgi_og.time_per_epoch]
            results[d]['dgi+xm_time'] = [dgi_plus.time_per_epoch]
            results[d]['error_og'] = [error_og]
            results[d]['error_plus'] = [error_plus]

            results[d]['embed_og'] = [embed_og]
            results[d]['embed_plus'] = [embed_plus]

        with open('./results/squirrel_dgi.pkl', 'wb') as file: 
            pkl.dump(results, file)


 15%|██████                                  | 382/2500 [00:11<01:03, 33.45it/s]


 24%|█████████▌                              | 595/2500 [00:17<00:56, 33.53it/s]

  4%|█▍                                       | 88/2500 [00:07<03:33, 11.31it/s]


 11%|████▌                                   | 282/2500 [00:24<03:11, 11.55it/s]


 19%|███████▌                                | 476/2500 [00:41<02:58, 11.33it/s]


 27%|██████████▌                             | 663/2500 [00:59<02:39, 11.49it/s]


...

 36%|███████████▊                     | 1869/5201 [24:00:52<89:24:03, 96.59s/it]


 38%|████████████▍                    | 1966/5201 [26:37:11<86:40:17, 96.45s/it]


 40%|███████████▌                 | 2063/5201 [31:20:33<1024:06:10, 1174.88s/it]


 50%|█████████████████▌                 | 1/2 [37:11:37<37:11:37, 133897.14s/it]


KeyboardInterrupt: 

In [82]:
fig = go.Figure()
fig.add_trace(go.Heatmap(z = explain_og,
                         x = list(sense_feat_dict), 
                         ))
fig.update_layout(title_text = 'DGI : ' + str(np.linalg.norm(explain_og, ord = 'nuc')), 
                  xaxis_title_text = 'Sense Features', 
                  yaxis_title_text = 'Dimensions')

fig.show()

fig = go.Figure()
fig.add_trace(go.Heatmap(z = explain_plus,
                         x = list(sense_feat_dict), 
                         ))
fig.update_layout(title_text = 'DGI+ : ' + str(np.linalg.norm(explain_plus, ord = 'nuc')), 
                  xaxis_title_text = 'Sense Features', 
                  yaxis_title_text = 'Dimensions')

fig.show()

In [97]:
Y_plus = embed_plus
sense_mat = tf.einsum('ij, ik -> ijk', Y_plus, sense_features)
Y_plus_norm = tf.linalg.diag_part(tf.matmul(Y_plus, Y_plus, transpose_b = True), k = 0)
sense_norm = tf.linalg.diag_part(tf.matmul(sense_features, sense_features, transpose_b = True), k = 0)
norm = Y_plus_norm * tf.cast(sense_norm, tf.float32)
D_plus = tf.transpose(tf.transpose(sense_mat) / norm)
D_plus = (D_plus - tf.reshape(tf.reduce_min(D_plus, axis = [-1, -2]), (-1, 1, 1))) / tf.reshape(tf.reduce_max(D_plus, axis = [-1, -2]) - tf.reduce_min(D_plus, axis = [-1, -2]), (-1, 1, 1))


Y_og = embed_og
sense_mat = tf.einsum('ij, ik -> ijk', Y_og, sense_features)
Y_og_norm = tf.linalg.diag_part(tf.matmul(Y_og, Y_og, transpose_b = True), k = 0)
sense_norm = tf.linalg.diag_part(tf.matmul(sense_features, sense_features, transpose_b = True), k = 0)
norm = Y_og_norm * tf.cast(sense_norm, tf.float32)
D_og = tf.transpose(tf.transpose(sense_mat) / norm)
D_og = (D_og - tf.reshape(tf.reduce_min(D_og, axis = [-1, -2]), (-1, 1, 1))) / tf.reshape(tf.reduce_max(D_og, axis = [-1, -2]) - tf.reduce_min(D_og, axis = [-1, -2]), (-1, 1, 1))


In [98]:

np.mean(norm_plus)

5.684189

In [99]:
norm_og = [np.linalg.norm(D_og[node, :, :], ord = 'nuc') for node in tqdm(range(len(graph)))]
norm_plus = [np.linalg.norm(D_plus[node, :, :], ord = 'nuc') for node in tqdm(range(len(graph)))]



100%|███████████████████████████████████████| 1186/1186 [02:45<00:00,  7.16it/s]


In [34]:
diff = np.array(norm_og) - np.array(norm_plus)
fig = go.Figure()
fig.add_trace(go.Histogram(x = diff))
fig.update_layout(title_text = 'Distribution of Difference In Nuclear Norms - DGI vs DGI+XM', 
                  xaxis_title_text = 'Difference In Nuclear Norms - DGI vs DGI+XM', 
                  yaxis_title_text = 'Frequency', 
                  plot_bgcolor = 'white', 
                  paper_bgcolor = 'white', 
                  font = dict(size = 30))
fig.show()

In [86]:
fig = go.Figure()

fig.add_trace(go.Histogram(x = norm_og, 
                           name = 'DGI'))
fig.add_trace(go.Histogram(x = norm_plus, 
                           name = 'DGI+XM'))


fig.update_layout(title_text = 'Distribution of Nuclear Norm of Node Explain Matrix', 
                  xaxis_title_text = 'Nuclear Norm', 
                  yaxis_title_text = 'Frequency', 
                  paper_bgcolor = 'white', 
                  plot_bgcolor = 'white', 
                  font = dict(size = 20))
fig.show()

In [57]:
fig = go.Figure()
fig.add_trace(go.Heatmap(z = D_plus[110, :, :]))

In [58]:
fig = go.Figure()
fig.add_trace(go.Heatmap(z = D_og[110, :, :]))

### LP - Remove

In [108]:
def decoder_model(input_shape):
    
    node_a = Input(shape = input_shape)
    node_b = Input(shape = input_shape)
    
    X = Concatenate()([node_a, node_b])
    X = Dense(64, activation = 'relu')(X)
    X = Dense(64, activation = 'relu')(X)
    X = Dense(1, activation = 'sigmoid')(X)
    
    return Model(inputs = [node_a, node_b], outputs = X)

def link_preidction(graph, embed_og, embed_plus, epochs):
    
    ig = igraph.Graph([[e[0], e[1]] for e in nx.to_edgelist(graph)])
    pos_edges = set(ig.get_edgelist())
    neg_indices = np.where(nx.to_numpy_array(graph) == 0)
    
    train_size = int(0.6 * len(pos_edges))
    test_size = int(0.4 * len(pos_edges))
    
    neg_edges = set()
    
    while len(neg_edges) <= 0.8 * len(pos_edges):

        idx = np.random.randint(neg_indices[0].shape[0])
        while neg_indices[0][idx] == neg_indices[1][idx]:
            idx = np.random.randint(neg_indices[0].shape[0])
        neg_edges.add((neg_indices[0][idx], neg_indices[1][idx]))
        print("Number of Negative Edges : " + str(len(neg_edges)), end = '\r')
        
    assert pos_edges.intersection(neg_edges) == set()
    
    pos_edges_idx = np.random.choice(range(len(pos_edges)), size = len(neg_edges), replace = False)

    pos_edges = np.array(list(pos_edges))[pos_edges_idx]
    neg_edges = np.array(list(neg_edges))
    
    assert pos_edges.shape[0] == neg_edges.shape[0]
    
    #####################################
    ######### Train On OG Embed #########
    #####################################
    embed = embed_og
    train_idx = np.random.choice(range(neg_edges.shape[0]), size = int(0.6 * len(neg_edges)), replace = False)
    test_idx = list(set(range(neg_edges.shape[0])).difference(set(train_idx)))
    assert set(train_idx).intersection(set(test_idx)) == set()

    # Placeholder Arrays
    train_node_0 = np.zeros((2 * train_idx.shape[0], embed.shape[1]))
    train_node_1 = np.zeros((2 * train_idx.shape[0], embed.shape[1]))

    test_node_0 = np.zeros((2 * len(test_idx), embed.shape[1]))
    test_node_1 = np.zeros((2 * len(test_idx), embed.shape[1]))

    # Train Data
    train_pos = pos_edges[train_idx]
    train_neg = neg_edges[train_idx]
    train_x = np.vstack([train_pos, train_neg])

    train_y_pos = np.ones((train_pos.shape[0], 1))
    train_y_neg = np.zeros((train_neg.shape[0], 1))
    train_y = np.vstack([train_y_pos, train_y_neg])

    for idx in tqdm(range(train_x.shape[0])):
        train_node_0[idx, :] = embed[train_x[idx][0]]
        train_node_1[idx, :] = embed[train_x[idx][1]]

    # Test Data
    test_pos = pos_edges[test_idx]
    test_neg = neg_edges[test_idx]
    test_x = np.vstack([test_pos, test_neg])

    test_y_pos = np.ones((test_pos.shape[0], 1))
    test_y_neg = np.zeros((test_neg.shape[0], 1))
    test_y = np.vstack([test_y_pos, test_y_neg])

    for idx in tqdm(range(test_x.shape[0])):
        test_node_0[idx, :] = embed[test_x[idx][0]]
        test_node_1[idx, :] = embed[test_x[idx][1]]

    # Class Balance
    assert train_pos.shape[0] == train_neg.shape[0]
    assert test_pos.shape[0] == test_neg.shape[0]
    
    model_og = decoder_model(input_shape = embed.shape[1])
    model_og.compile(loss = tf.keras.losses.binary_crossentropy,
                  optimizer = tf.keras.optimizers.Adam(learning_rate = 1e-4),
                  metrics = ["accuracy"])
    history = model_og.fit([train_node_0, train_node_1], train_y, epochs = epochs)
    _, og_acc = model_og.evaluate([test_node_0, test_node_1], test_y)
    og_pred = model_og.predict([test_node_0, test_node_1])
    og_auc = roc_auc_score(test_y, og_pred)
    og_aup = average_precision_score(test_y, og_pred)
    
    #####################################
    ######### Train On XM Embed #########
    #####################################
    embed = embed_plus
    train_idx = np.random.choice(range(neg_edges.shape[0]), size = int(0.6 * len(neg_edges)), replace = False)
    test_idx = list(set(range(neg_edges.shape[0])).difference(set(train_idx)))
    assert set(train_idx).intersection(set(test_idx)) == set()

    # Placeholder Arrays
    train_node_0 = np.zeros((2 * train_idx.shape[0], embed.shape[1]))
    train_node_1 = np.zeros((2 * train_idx.shape[0], embed.shape[1]))

    test_node_0 = np.zeros((2 * len(test_idx), embed.shape[1]))
    test_node_1 = np.zeros((2 * len(test_idx), embed.shape[1]))

    # Train Data
    train_pos = pos_edges[train_idx]
    train_neg = neg_edges[train_idx]
    train_x = np.vstack([train_pos, train_neg])

    train_y_pos = np.ones((train_pos.shape[0], 1))
    train_y_neg = np.zeros((train_neg.shape[0], 1))
    train_y = np.vstack([train_y_pos, train_y_neg])

    for idx in tqdm(range(train_x.shape[0])):
        train_node_0[idx, :] = embed[train_x[idx][0]]
        train_node_1[idx, :] = embed[train_x[idx][1]]

    # Test Data
    test_pos = pos_edges[test_idx]
    test_neg = neg_edges[test_idx]
    test_x = np.vstack([test_pos, test_neg])

    test_y_pos = np.ones((test_pos.shape[0], 1))
    test_y_neg = np.zeros((test_neg.shape[0], 1))
    test_y = np.vstack([test_y_pos, test_y_neg])

    for idx in tqdm(range(test_x.shape[0])):
        test_node_0[idx, :] = embed[test_x[idx][0]]
        test_node_1[idx, :] = embed[test_x[idx][1]]

    # Class Balance
    assert train_pos.shape[0] == train_neg.shape[0]
    assert test_pos.shape[0] == test_neg.shape[0]
    
    model_plus = decoder_model(input_shape = embed.shape[1])
    model_plus.compile(loss = tf.keras.losses.binary_crossentropy,
                  optimizer = tf.keras.optimizers.Adam(learning_rate = 1e-4),
                  metrics = ["accuracy"])
    history = model_plus.fit([train_node_0, train_node_1], train_y, epochs = epochs)
    _, plus_acc = model_plus.evaluate([test_node_0, test_node_1], test_y)
    plus_pred = model_plus.predict([test_node_0, test_node_1])
    plus_auc = roc_auc_score(test_y, plus_pred)
    plus_aup = average_precision_score(test_y, plus_pred)
    
    
    return {'plus_acc' : plus_acc, 
            'plus_auc' : plus_auc, 
            'plus_aup' : plus_aup, 
            'og_acc' : og_acc,
            'og_auc' : og_auc, 
            'og_aup' : og_aup}

In [116]:
with open('./results/squirrel_lp.pkl', 'rb') as file: 
        squirrel_results = pkl.load(file)

In [117]:
squirrel_results

{'dgi': array([[0.97051471, 0.9951491 , 0.99612948, 0.98575711, 0.99917932,
         0.99929206],
        [0.98150927, 0.99647802, 0.99731935, 0.9802599 , 0.99753971,
         0.99807126],
        [0.98050976, 0.99823726, 0.99851422, 0.98100948, 0.99819231,
         0.99844505]]),
 'sdne': array([[0.92978513, 0.98770717, 0.98623317, 0.9830085 , 0.99848402,
         0.99870384],
        [0.97151423, 0.99558592, 0.99653863, 0.98725635, 0.99786613,
         0.99865792],
        [0.97726136, 0.9968524 , 0.99730575, 0.97776109, 0.99840684,
         0.99859982]]),
 'line': array([[0.98325837, 0.99743157, 0.9984368 , 0.99025488, 0.99945704,
         0.99948016],
        [0.9862569 , 0.99829096, 0.99871276, 0.98750627, 0.99885065,
         0.99895928],
        [0.99350327, 0.99795729, 0.9987544 , 0.98150927, 0.99900874,
         0.99924001]])}

In [ ]:
with open('./data/squirrel.pkl', 'rb') as file: 
    graph = pkl.load(file)
graph = nx.Graph(nx.to_numpy_array(graph))


try:
    with open('./results/squirrel_lp.pkl', 'rb') as file: 
        squirrel_results = pkl.load(file)
except:
    print ("Warning, will overwrite any existing results file")
    squirrel_results = {}
dim = 128

###################
####### gmi #######
###################
with open('./results/squirrel_gmi.pkl', 'rb') as file:
    results = pkl.load(file)
runs = len(results[dim]['norm_og'])
random_idx = np.random.randint(runs)
    
lp_results = []
for _ in tqdm(range(3)):
    
    runs = len(results[dim]['norm_og'])
    random_idx = np.random.randint(runs)
    print ("Using Run #" + str(random_idx))
    lp_dict = link_preidction(graph = graph,
                              embed_og = results[dim]['embed_og'][random_idx],
                              embed_plus = results[dim]['embed_plus'][random_idx],
                              epochs = 100)
    lp_results.append(list(lp_dict.values()))
    
lp_results = np.array(lp_results)
squirrel_results['gmi'] = lp_results

gmi_norm = np.nanmean(results[dim]['norm_og'])
gmi_norm_std = np.nanstd(results[dim]['norm_og'])

gmi_xm_norm = np.nanmean(results[dim]['norm_plus'])
gmi_xm_norm_std = np.nanstd(results[dim]['norm_plus'])

with open('./results/squirrel_lp.pkl', 'wb') as file: 
    pkl.dump(squirrel_results, file)



  0%|                                                       | 0/3 [00:00<?, ?it/s]

Using Run #2
Number of Negative Edges : 67454

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)


100%|████████████████████████████████| 190554/190554 [00:00<00:00, 1007098.47it/s]

100%|█████████████████████████████████| 127036/127036 [00:00<00:00, 977285.17it/s]


Epoch 1/100
   1/5955 [..............................] - ETA: 30:07 - loss: 0.7071 - accuracy: 0.5312

2023-01-25 11:13:16.442102: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:114] Plugin optimizer for device_type GPU is enabled.


5955/5955 [==============================] - 44s 7ms/step - loss: 0.3240 - accuracy: 0.8873
Epoch 2/100
2628/5955 [============>.................] - ETA: 23s - loss: 0.2506 - accuracy: 0.9053